In [1]:
# Python ≥3.5 is required
import sys
assert sys.version_info >= (3, 5)

# Scikit-Learn ≥0.20 is required
import sklearn
assert sklearn.__version__ >= "0.20"

try:
    # %tensorflow_version only exists in Colab.
    %tensorflow_version 2.x
except Exception:
    pass

import tensorflow as tf
assert tf.__version__ >= "2.0"

# Common imports
import numpy as np
import os

# to make this notebook's output stable across runs
np.random.seed(42)

# To plot pretty figures
%matplotlib inline
import matplotlib as mpl
import matplotlib.pyplot as plt
mpl.rc('axes', labelsize=14)
mpl.rc('xtick', labelsize=12)
mpl.rc('ytick', labelsize=12)

# Where to save the figures
PROJECT_ROOT_DIR = "."
CHAPTER_ID = "ann"
IMAGES_PATH = os.path.join(PROJECT_ROOT_DIR, "images", CHAPTER_ID)

# Ignore useless warnings (see SciPy issue #5998)
import warnings
warnings.filterwarnings(action="ignore", message="^internal gelsd")
impoe

In [2]:
from sklearn.datasets import fetch_california_housing
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
housing = fetch_california_housing()
X_train_full, X_test, y_train_full, y_test = train_test_split(
housing.data, housing.target)
X_train, X_valid, y_train, y_valid = train_test_split(
X_train_full, y_train_full)
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_valid = scaler.transform(X_valid)
X_test = scaler.transform(X_test)

In [5]:
import tensorflow as tf
from tensorflow import keras
tf.__version__
keras.__version__

'2.2.4-tf'

In [22]:
model = keras.models.Sequential([
keras.layers.Dense(30, activation="relu",
input_shape=X_train.shape[1:]),
keras.layers.Dense(1)
])
model.compile(loss="mean_squared_error", optimizer="sgd")
history = model.fit(X_train, y_train, epochs=20,
validation_data=(X_valid, y_valid))
mse_test = model.evaluate(X_test, y_test)
X_new = X_test[:3] # pretend these are new instances
y_pred = model.predict(X_new)

Train on 11610 samples, validate on 3870 samples
Epoch 1/20
11610/11610 [==============================] - 1s 104us/sample - loss: 1.5548 - val_loss: 0.5733
Epoch 2/20
11610/11610 [==============================] - 1s 48us/sample - loss: 0.5109 - val_loss: 0.5156
Epoch 3/20
11610/11610 [==============================] - 1s 48us/sample - loss: 0.4563 - val_loss: 0.6769
Epoch 4/20
11610/11610 [==============================] - 1s 47us/sample - loss: 0.4365 - val_loss: 0.4586
Epoch 5/20
11610/11610 [==============================] - 1s 54us/sample - loss: 0.4166 - val_loss: 0.4438
Epoch 6/20
11610/11610 [==============================] - 1s 47us/sample - loss: 0.4099 - val_loss: 0.4399
Epoch 7/20
11610/11610 [==============================] - 1s 55us/sample - loss: 0.4053 - val_loss: 0.4295
Epoch 8/20
11610/11610 [==============================] - 1s 49us/sample - loss: 0.3991 - val_loss: 0.4274
Epoch 9/20
11610/11610 [==============================] - 1s 47us/sample - loss: 0.3927 - val_

In [23]:
input_ = keras.layers.Input(shape=X_train.shape[1:])
hidden1 = keras.layers.Dense(30, activation="relu")(input_)
hidden2 = keras.layers.Dense(30, activation="relu")(hidden1)
concat = keras.layers.Concatenate()([input_, hidden2])
output = keras.layers.Dense(1)(concat)
model = keras.Model(inputs=[input_], outputs=[output])

In [24]:
input_A = keras.layers.Input(shape=[5], name="wide_input")
input_B = keras.layers.Input(shape=[6], name="deep_input")
hidden1 = keras.layers.Dense(30, activation="relu")(input_B)
hidden2 = keras.layers.Dense(30, activation="relu")(hidden1)
concat = keras.layers.concatenate([input_A, hidden2])
output = keras.layers.Dense(1, name="output")(concat)
model = keras.Model(inputs=[input_A, input_B], outputs=[output])

In [25]:
model.compile(loss="mse", optimizer=keras.optimizers.SGD(lr=1e-3))
X_train_A, X_train_B = X_train[:, :5], X_train[:, 2:]
X_valid_A, X_valid_B = X_valid[:, :5], X_valid[:, 2:]
X_test_A, X_test_B = X_test[:, :5], X_test[:, 2:]
X_new_A, X_new_B = X_test_A[:3], X_test_B[:3]
history = model.fit((X_train_A, X_train_B), y_train, epochs=20,
validation_data=((X_valid_A, X_valid_B), y_valid))
mse_test = model.evaluate((X_test_A, X_test_B), y_test)
y_pred = model.predict((X_new_A, X_new_B))

Train on 11610 samples, validate on 3870 samples
Epoch 1/20
11610/11610 [==============================] - 1s 92us/sample - loss: 2.2064 - val_loss: 0.9430
Epoch 2/20
11610/11610 [==============================] - 1s 54us/sample - loss: 0.7638 - val_loss: 0.6631
Epoch 3/20
11610/11610 [==============================] - 1s 54us/sample - loss: 0.6165 - val_loss: 0.5995
Epoch 4/20
11610/11610 [==============================] - 1s 53us/sample - loss: 0.5670 - val_loss: 0.5685
Epoch 5/20
11610/11610 [==============================] - 1s 54us/sample - loss: 0.5390 - val_loss: 0.5455
Epoch 6/20
11610/11610 [==============================] - 1s 53us/sample - loss: 0.5197 - val_loss: 0.5318
Epoch 7/20
11610/11610 [==============================] - 1s 53us/sample - loss: 0.5056 - val_loss: 0.5202
Epoch 8/20
11610/11610 [==============================] - 1s 54us/sample - loss: 0.4952 - val_loss: 0.5109
Epoch 9/20
11610/11610 [==============================] - 1s 55us/sample - loss: 0.4869 - val_l

In [11]:
model.compile(loss=["mse"], loss_weights=[0.9, 0.1],
optimizer="sgd")

ValueError: When passing a list as loss_weights, it should have one entry per model output. The model has 1 outputs, but you passed loss_weights=[0.9, 0.1]

In [ ]:
history = model.fit(
[X_train_A, X_train_B], [y_train, y_train], epochs=20,
validation_data=([X_valid_A, X_valid_B], [y_valid, y_valid]))

In [ ]:
total_loss, main_loss, aux_loss = model.evaluate(
[X_test_A, X_test_B], [y_test, y_test])


In [ ]:
y_pred_main, y_pred_aux = model.predict([X_new_A, X_new_B])

In [12]:
class WideAndDeepModel(keras.Model):
    def __init__(self, units=30, activation="relu", **kwargs):
        super().__init__(**kwargs)
        self.hidden1 = keras.layers.Dense(units, activation=activation)
        self.hidden2 = keras.layers.Dense(units, activation=activation)
        self.main_output = keras.layers.Dense(1)
        self.aux_output = keras.layers.Dense(1)
        
    def call(self, inputs):
        input_A, input_B = inputs
        hidden1 = self.hidden1(input_B)
        hidden2 = self.hidden2(hidden1)
        concat = keras.layers.concatenate([input_A, hidden2])
        main_output = self.main_output(concat)
        aux_output = self.aux_output(hidden2)
        return main_output, aux_output

In [13]:
model = WideAndDeepModel()

In [15]:
checkpoint_cb = keras.callbacks.ModelCheckpoint("my_kears_model.h5")
history = model.fit(X_train, y_train, epochs = 10, callbacks=[checkpoint_cb])

ValueError: ('Could not interpret optimizer identifier:', Ellipsis)

In [16]:
import os
root_logdir = os.path.join(os.curdir, "my_logs")

In [19]:
def get_run_logdir():
    import time
    run_id = time.strftime("run_%Y_%m_%d-%H_%M_%S")
    return os.path.join(root_logdir, run_id)

run_logdir = get_run_logdir()
run_logdir

'.\\my_logs\\run_2020_06_13-15_10_42'

In [32]:
model = keras.models.Sequential([
keras.layers.Dense(30, activation="relu",
input_shape=X_train.shape[1:]),
keras.layers.Dense(1)
])
model.compile(loss="mean_squared_error", optimizer=keras.optimizers.SGD(lr=0.05))

In [33]:
tensorboard_cb = keras.callbacks.TensorBoard(run_logdir)
history = model.fit(X_train, y_train, epochs = 30,
                   validation_data = (X_valid, y_valid),
                   callbacks= [tensorboard_cb])

Train on 11610 samples, validate on 3870 samples
Epoch 1/30
11610/11610 [==============================] - 1s 90us/sample - loss: nan - val_loss: nan
Epoch 2/30
11610/11610 [==============================] - 1s 48us/sample - loss: nan - val_loss: nan
Epoch 3/30
11610/11610 [==============================] - 1s 47us/sample - loss: nan - val_loss: nan
Epoch 4/30
11610/11610 [==============================] - 1s 47us/sample - loss: nan - val_loss: nan
Epoch 5/30
11610/11610 [==============================] - 1s 53us/sample - loss: nan - val_loss: nan
Epoch 6/30
11610/11610 [==============================] - 1s 51us/sample - loss: nan - val_loss: nan
Epoch 7/30
11610/11610 [==============================] - 1s 51us/sample - loss: nan - val_loss: nan
Epoch 8/30
11610/11610 [==============================] - 1s 49us/sample - loss: nan - val_loss: nan
Epoch 9/30
11610/11610 [==============================] - 1s 62us/sample - loss: nan - val_loss: nan
Epoch 10/30
11610/11610 [=================

In [30]:
%load_ext tensorboard
%tensorboard --logdir=./my_logs --port=6006

ERROR: Timed out waiting for TensorBoard to start. It may still be running as pid 5668.

In [35]:
test_logdir = get_run_logdir()
writer = tf.summary.create_file_writer(test_logdir)
with writer.as_default():
    for step in range(1, 1000 + 1):
        tf.summary.scalar("my_scalar", np.sin(step / 10), step=step)
        data = (np.random.randn(100) + 2) * step / 100 # some random data
        tf.summary.histogram("my_hist", data, buckets=50, step=step)
        images = np.random.rand(2, 32, 32, 3) # random 32×32 RGB images
        tf.summary.image("my_images", images * step / 1000, step=step)
        texts = ["The step is " + str(step), "Its square is " +str(step**2)]
        tf.summary.text("my_text", texts, step=step)
        sine_wave = tf.math.sin(tf.range(12000) / 48000 * 2 * np.pi * step)
        audio = tf.reshape(tf.cast(sine_wave, tf.float32), [1, -1, 1])
        tf.summary.audio("my_audio", audio, sample_rate=48000, step=step)

In [40]:
def build_model(n_hidden = 1, n_neurons= 30, learning_rate = 3e-3,
               input_shape=[8]):
    model = keras.models.Sequential()
    model.add(keras.layers.InputLayer(input_shape = input_shape))
    for layer in range(n_hidden):
        model.add(keras.layers.Dense(n_neurons, activation="relu"))
    model.add(keras.layers.Dense(1))
    optimizer = keras.optimizers.SGD(lr =learning_rate)
    model.compile(loss="mse", optimizer = optimizer)
    return model

In [41]:
keras_reg = keras.wrappers.scikit_learn.KerasRegressor(build_model)

In [42]:
keras_reg.fit(X_train, y_train, epochs=100,
             validation_data = (X_valid, y_valid),
             callbacks=[keras.callbacks.EarlyStopping(patience=10)])
mse_test = keras_reg.score(X_test, y_test)
y_pred = keras_reg.predict(X_new)

Train on 11610 samples, validate on 3870 samples
Epoch 1/100
11610/11610 [==============================] - 1s 76us/sample - loss: 1.4644 - val_loss: 0.6778
Epoch 2/100
11610/11610 [==============================] - 1s 49us/sample - loss: 0.6370 - val_loss: 0.6004
Epoch 3/100
11610/11610 [==============================] - 1s 46us/sample - loss: 0.5552 - val_loss: 0.5402
Epoch 4/100
11610/11610 [==============================] - 1s 48us/sample - loss: 0.5140 - val_loss: 0.5167
Epoch 5/100
11610/11610 [==============================] - 1s 48us/sample - loss: 0.4905 - val_loss: 0.5004
Epoch 6/100
11610/11610 [==============================] - 1s 48us/sample - loss: 0.4756 - val_loss: 0.4868
Epoch 7/100
11610/11610 [==============================] - 1s 48us/sample - loss: 0.4641 - val_loss: 0.4790
Epoch 8/100
11610/11610 [==============================] - 1s 48us/sample - loss: 0.4563 - val_loss: 0.4707
Epoch 9/100
11610/11610 [==============================] - 1s 48us/sample - loss: 0.450

Epoch 76/100
11610/11610 [==============================] - 1s 45us/sample - loss: 0.3619 - val_loss: 0.3946
Epoch 77/100
11610/11610 [==============================] - 1s 44us/sample - loss: 0.3636 - val_loss: 0.3938
Epoch 78/100
11610/11610 [==============================] - 1s 45us/sample - loss: 0.3609 - val_loss: 0.3944
Epoch 79/100
11610/11610 [==============================] - 1s 46us/sample - loss: 0.3609 - val_loss: 0.3928
Epoch 80/100
11610/11610 [==============================] - 1s 47us/sample - loss: 0.3625 - val_loss: 0.3913
Epoch 81/100
11610/11610 [==============================] - 1s 47us/sample - loss: 0.3593 - val_loss: 0.3934
Epoch 82/100
11610/11610 [==============================] - 1s 45us/sample - loss: 0.3601 - val_loss: 0.3931
Epoch 83/100
11610/11610 [==============================] - 1s 48us/sample - loss: 0.3598 - val_loss: 0.3915
Epoch 84/100
11610/11610 [==============================] - 1s 48us/sample - loss: 0.3587 - val_loss: 0.3949
Epoch 85/100
11610/

In [44]:
from scipy.stats import reciprocal
from sklearn.model_selection import RandomizedSearchCV

param_distribs = {
    "n_hidden": [0,1,2,3],
    "n_neurons": np.arange(1,100),
    "learning_rate": reciprocal(3e-4, 3e-2)
}

In [45]:
rnd_search_cv = RandomizedSearchCV(keras_reg, param_distribs, n_iter = 10, cv =3)
rnd_search_cv.fit(X_train, y_train, epochs=100,
                 validation_data = (X_valid, y_valid),
                 callbacks=[keras.callbacks.EarlyStopping(patience=10)])

Train on 7740 samples, validate on 3870 samples
Epoch 1/100
7740/7740 [==============================] - 1s 116us/sample - loss: 3.2292 - val_loss: 1.4771
Epoch 2/100
7740/7740 [==============================] - 0s 58us/sample - loss: 1.0409 - val_loss: 0.8579
Epoch 3/100
7740/7740 [==============================] - 0s 56us/sample - loss: 0.7520 - val_loss: 0.7158
Epoch 4/100
7740/7740 [==============================] - 0s 60us/sample - loss: 0.6770 - val_loss: 0.6761
Epoch 5/100
7740/7740 [==============================] - 0s 61us/sample - loss: 0.6476 - val_loss: 0.6549
Epoch 6/100
7740/7740 [==============================] - 0s 59us/sample - loss: 0.6279 - val_loss: 0.6366
Epoch 7/100
7740/7740 [==============================] - 0s 55us/sample - loss: 0.6103 - val_loss: 0.6195
Epoch 8/100
7740/7740 [==============================] - 0s 61us/sample - loss: 0.5942 - val_loss: 0.6062
Epoch 9/100
7740/7740 [==============================] - 0s 56us/sample - loss: 0.5791 - val_loss: 0.59

7740/7740 [==============================] - 0s 56us/sample - loss: 0.3719 - val_loss: 0.4093
Epoch 78/100
7740/7740 [==============================] - 0s 56us/sample - loss: 0.3707 - val_loss: 0.4078
Epoch 79/100
7740/7740 [==============================] - 0s 56us/sample - loss: 0.3702 - val_loss: 0.4075
Epoch 80/100
7740/7740 [==============================] - 0s 56us/sample - loss: 0.3687 - val_loss: 0.4057
Epoch 81/100
7740/7740 [==============================] - 0s 58us/sample - loss: 0.3681 - val_loss: 0.4061
Epoch 82/100
7740/7740 [==============================] - 0s 58us/sample - loss: 0.3672 - val_loss: 0.4052
Epoch 83/100
7740/7740 [==============================] - 0s 64us/sample - loss: 0.3666 - val_loss: 0.4032
Epoch 84/100
7740/7740 [==============================] - 0s 56us/sample - loss: 0.3654 - val_loss: 0.4025
Epoch 85/100
7740/7740 [==============================] - 0s 56us/sample - loss: 0.3646 - val_loss: 0.4065
Epoch 86/100
7740/7740 [==========================

Train on 7740 samples, validate on 3870 samples
Epoch 1/100
7740/7740 [==============================] - 1s 115us/sample - loss: 2.1254 - val_loss: 0.9625
Epoch 2/100
7740/7740 [==============================] - 0s 56us/sample - loss: 0.7688 - val_loss: 0.7021
Epoch 3/100
7740/7740 [==============================] - 0s 56us/sample - loss: 0.6494 - val_loss: 0.6627
Epoch 4/100
7740/7740 [==============================] - 1s 67us/sample - loss: 0.6161 - val_loss: 0.6419
Epoch 5/100
7740/7740 [==============================] - 0s 56us/sample - loss: 0.5945 - val_loss: 0.6225
Epoch 6/100
7740/7740 [==============================] - 0s 56us/sample - loss: 0.5757 - val_loss: 0.6053
Epoch 7/100
7740/7740 [==============================] - 0s 60us/sample - loss: 0.5595 - val_loss: 0.5905
Epoch 8/100
7740/7740 [==============================] - 1s 67us/sample - loss: 0.5449 - val_loss: 0.5764
Epoch 9/100
7740/7740 [==============================] - 1s 69us/sample - loss: 0.5317 - val_loss: 0.56

7740/7740 [==============================] - 0s 63us/sample - loss: 0.3537 - val_loss: 0.3989
Epoch 78/100
7740/7740 [==============================] - 0s 58us/sample - loss: 0.3531 - val_loss: 0.3985
Epoch 79/100
7740/7740 [==============================] - 0s 56us/sample - loss: 0.3519 - val_loss: 0.3952
Epoch 80/100
7740/7740 [==============================] - 0s 58us/sample - loss: 0.3508 - val_loss: 0.3960
Epoch 81/100
7740/7740 [==============================] - 0s 58us/sample - loss: 0.3500 - val_loss: 0.3956
Epoch 82/100
7740/7740 [==============================] - 0s 56us/sample - loss: 0.3495 - val_loss: 0.3954
Epoch 83/100
7740/7740 [==============================] - 0s 56us/sample - loss: 0.3484 - val_loss: 0.3948
Epoch 84/100
7740/7740 [==============================] - 0s 56us/sample - loss: 0.3475 - val_loss: 0.3942
Epoch 85/100
7740/7740 [==============================] - 0s 60us/sample - loss: 0.3472 - val_loss: 0.3925
Epoch 86/100
7740/7740 [==========================

Train on 7740 samples, validate on 3870 samples
Epoch 1/100
7740/7740 [==============================] - 1s 140us/sample - loss: 2.1110 - val_loss: 1.0137
Epoch 2/100
7740/7740 [==============================] - 0s 57us/sample - loss: 0.9222 - val_loss: 0.8133
Epoch 3/100
7740/7740 [==============================] - 0s 57us/sample - loss: 0.7929 - val_loss: 0.7367
Epoch 4/100
7740/7740 [==============================] - 0s 58us/sample - loss: 0.7283 - val_loss: 0.6893
Epoch 5/100
7740/7740 [==============================] - 0s 64us/sample - loss: 0.6820 - val_loss: 0.6507
Epoch 6/100
7740/7740 [==============================] - 1s 91us/sample - loss: 0.6449 - val_loss: 0.6194
Epoch 7/100
7740/7740 [==============================] - 0s 58us/sample - loss: 0.6133 - val_loss: 0.5927
Epoch 8/100
7740/7740 [==============================] - 0s 60us/sample - loss: 0.5871 - val_loss: 0.5691
Epoch 9/100
7740/7740 [==============================] - 0s 57us/sample - loss: 0.5663 - val_loss: 0.55

...

7740/7740 [==============================] - 0s 58us/sample - loss: 0.2671 - val_loss: 0.3321
Epoch 78/100
7740/7740 [==============================] - 0s 59us/sample - loss: 0.2633 - val_loss: 0.3376
Epoch 79/100
7740/7740 [==============================] - 0s 59us/sample - loss: 0.2659 - val_loss: 0.3239
Epoch 80/100
7740/7740 [==============================] - 0s 58us/sample - loss: 0.2640 - val_loss: 0.3387
Epoch 81/100
7740/7740 [==============================] - 0s 58us/sample - loss: 0.2624 - val_loss: 0.3281
3870/1 [======================================================================================================================================================================================================================================================================================================================================================================================================================================================================================

Train on 7740 samples, validate on 3870 samples
Epoch 1/100
7740/7740 [==============================] - 1s 108us/sample - loss: 1.2790 - val_loss: 1.5760
Epoch 2/100
7740/7740 [==============================] - 0s 59us/sample - loss: 2.6361 - val_loss: 5.9593
Epoch 3/100
7740/7740 [==============================] - 0s 61us/sample - loss: nan - val_loss: nan
Epoch 4/100
3456/7740 [============>.................] - ETA: 0s - loss: nan

C:\Users\Hwan\AppData\Roaming\Python\Python37\site-packages\tensorflow_core\python\keras\callbacks.py:1225: RuntimeWarning: invalid value encountered in less
  if self.monitor_op(current - self.min_delta, self.best):


7740/7740 [==============================] - 0s 59us/sample - loss: nan - val_loss: nan
Epoch 5/100
7740/7740 [==============================] - 0s 58us/sample - loss: nan - val_loss: nan
Epoch 6/100
7740/7740 [==============================] - 0s 58us/sample - loss: nan - val_loss: nan
Epoch 7/100
7740/7740 [==============================] - 0s 58us/sample - loss: nan - val_loss: nan
Epoch 8/100
7740/7740 [==============================] - 0s 58us/sample - loss: nan - val_loss: nan
Epoch 9/100
7740/7740 [==============================] - 0s 58us/sample - loss: nan - val_loss: nan
Epoch 10/100
7740/7740 [==============================] - 0s 62us/sample - loss: nan - val_loss: nan
Epoch 11/100
7740/7740 [==============================] - 0s 58us/sample - loss: nan - val_loss: nan
3870/1 [==========================================================================================================================================================================================================

RuntimeError: Cannot clone object <tensorflow.python.keras.wrappers.scikit_learn.KerasRegressor object at 0x000002BDA575FCC8>, as the constructor either does not set or modifies parameter learning_rate

In [46]:
rnd_search_cv.best_params_

{'learning_rate': 0.004778223340688506, 'n_hidden': 2, 'n_neurons': 79}

In [47]:
rnd_search_cv.best_score_

-0.301636915259275

In [49]:
model = rnd_search_cv.best_estimator_.model

AttributeError: 'RandomizedSearchCV' object has no attribute 'best_estimator_'

In [50]:
model = keras.models.Sequential([
    keras.layers.Flatten(input_shape=[28, 28]),
    keras.layers.BatchNormalization(),
    keras.layers.Dense(300, activation="elu",
                      kernel_initializer="he_normal"),
    keras.layers.BatchNormalization(),
    keras.layers.Dense(100, activation="elu",
                      kernel_initializer="he_normal"),
    keras.layers.BatchNormalization(),
    keras.layers.Dense(10, activation="softmax")
])

In [51]:
model.summary()

Model: "sequential_37"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
flatten (Flatten)            (None, 784)               0         
_________________________________________________________________
batch_normalization (BatchNo (None, 784)               3136      
_________________________________________________________________
dense_104 (Dense)            (None, 300)               235500    
_________________________________________________________________
batch_normalization_1 (Batch (None, 300)               1200      
_________________________________________________________________
dense_105 (Dense)            (None, 100)               30100     
_________________________________________________________________
batch_normalization_2 (Batch (None, 100)               400       
_________________________________________________________________
dense_106 (Dense)            (None, 10)              

In [52]:
[(var.name, var.trainable) for var in model.layers[1].variables]

[('batch_normalization/gamma:0', True),
 ('batch_normalization/beta:0', True),
 ('batch_normalization/moving_mean:0', False),
 ('batch_normalization/moving_variance:0', False)]

In [55]:
model.layers[1].updates

[<tf.Operation 'cond/Identity' type=Identity>,
 <tf.Operation 'cond_1/Identity' type=Identity>]

In [ ]:
model = keras.models.Sequential([
    keras.layers.Flatten(input_shape=[28, 28]),
    keras.layers.BatchNormalization(),
    keras.layers.Dense(300, kernel_initializer="he_normal",
    use_bias=False),
    keras.layers.BatchNormalization(),
    keras.layers.Activation("elu"),
    keras.layers.Dense(100, kernel_initializer="he_normal",
    use_bias=False),
    keras.layers.BatchNormalization(),
    keras.layers.Activation("elu"),
    keras.layers.Dense(10, activation="softmax")
])